# Seminar Problemorientierte Programmierung

## Exkurs: Was mir an Python gefällt

In dieser Rubrik, die immer am Anfang eines Kapitels steht, möchte ich Ihnen zeigen, wofür ich Python nutze und warum ich es mag. Sie werden vielleicht noch nicht verstehen, was ich genau mache, aber Sie sehen damit schon einmal die Möglichkeiten von Python und können später darauf zurückgreifen. Da dies auch ein Exkurs ist, können Sie diese Rubrik gerne auch erst einmal überspringen.

Mit Hilfe von pydotplus ist es möglich, Graphen zu visualisieren, die auch direkt im Jupyter Notebook angezeigt werden können. Als Beispiel wird hier ein [Trie](https://de.wikipedia.org/wiki/Trie) erzeugt, der schnellen Zugriff auf die Präfixe einer Liste von Wörtern bildet (so etwas ermöglicht z.B. eine schnelle Wortvervollständigung bei der Eingabe von Wörtern auf der Handy-Tastatur ([siehe](https://towardsdatascience.com/implementing-a-trie-data-structure-in-python-in-less-than-100-lines-of-code-a877ea23c1a1)).

In [ ]:
from IPython.display import Image  
import pydotplus

# Der Quellcode für die Klasse TrieNode und die Funktion add stammt von der Webseite
# from https://towardsdatascience.com/implementing-a-trie-data-structure-in-python-in-less-than-100-lines-of-code-a877ea23c1a1
class TrieNode(object):
    def __init__(self, char: str):
        self.char = char
        self.children = []
        self.word = None
        self.counter = 1

def add(root, word):
    node = root
    for char in word:
        found_in_child = False
        # Search for the character in the children of the present `node`
        for child in node.children:
            if child.char == char:
                # We found it, increase the counter by 1 to keep track that another
                # word has it as well
                child.counter += 1
                # And point the node to the child that contains this char
                node = child
                found_in_child = True
                break
        # We did not find it so add a new chlid
        if not found_in_child:
            new_node = TrieNode(char)
            node.children.append(new_node)
            # And then point node to the new child
            node = new_node
    # Everything finished. Mark it as the end of a word.
    node.word = word

# fügt eine Liste von Wörtern hinzu
def add_words(root, words):
    for word in words:
        add(root, word)

# wandelt den Baum in einen Graphen, also eine Menge von Knoten (vertices) und Kanten (edges) um
# Eingaben:
# - root: Wurzelknoten des Baums
# - vertices: (leere) Liste mit Knoten (jeder Knoten ist vom Typ TrieNode)
# - edges: (leere) Liste mit Kanten (jede Kante ist ein Tupel von ganzen Zahlen, die die Knoten-IDs repräsentieren)
def tree_to_graph(root, vertices, edges):
    # Hinzufügen des Wurzelknotens
    if len(vertices) == 0:
        vertices.append(root)
    # wir nummerieren die Knoten durch:
    # jeder Knoten erhält als ID seine Position in der Liste (ab 1 zählend)
    rootid = len(vertices)
    # Hinzufügen der Kindknoten
    for child in root.children:
        vertices.append(child)
        childid = len(vertices)
        
        # Kante zum Kindknoten hinzufügen
        edges.append((rootid, childid))

        # Rekursion, falls Kindknoten vorhanden
        if child.children:
            tree_to_graph(child, vertices, edges)

# erzeugt eine Zeichenkette in der Syntax for GraphViz (http://graphviz.org/)
def build_graph_string(vertices, edges):
    # Konfiguration für Graph, Knoten und Kanten 
    s = """
digraph G {
  graph [rankdir="LR"];
  node [sep="+0.01,+0.01", height="0", width="0", shape="box", margin="0.05, 0.05"];
  edge [];
    """
    # Hinzufügen der Knoten
    for i, vertice in enumerate(vertices):
        label = vertice.char
        # Knoten, die ein Wort repräsentieren, sollen dieses zusätzlich enthalten
        if vertice.word:
            label += " (" + vertice.word + ")"
        s += '  ' + str(i + 1) + ' [label="' + label + '"];\n'
    # Hinzufügen der Kanten
    for v1, v2 in edges:
        s += '  ' + str(v1) + ' -> ' + str(v2) + ';\n'
    s += "}"
    return s
        

# Beispielwörter zum Visualisieren - ergänzen Sie die Liste oder probieren Sie andere Wörter
words = ["Braten", "Brauerei", "Brause", "Brot", "Brett", 
         "Brei", "Brief", "Breite", "Brille", "Brand", "Bruder", 
         "Bruch", "Brust", "Bronze", "Brache", "Branche", 
         "Brandung", "Braten", "Bratsche", "Bremse", "Brenner", 
         "Brezel", "Brikett", "Brise", "Brocken", "Bronze", 
         "Brosche", "Brunnen", "Brut"]
# Alternative: aus einer Datei einlesen
# words = []
# fin = open('top10000de.txt', encoding="latin1")
# for line in fin:
#     if line.startswith("Bra"):
#         words.append(line.strip())

# Wörter zum Trie hinzufügen (in sortierter Reihenfolge, das liest sich leichter)
root = TrieNode('*')
add_words(root, sorted(words))

# aus dem Trie einen Graph erzeugen
vertices = []
edges = []
tree_to_graph(root, vertices, edges)

# die Zeichenkette für GraphViz erzeugen
graphdata = build_graph_string(vertices, edges)

# den Graph zeichnen und anzeigen
graph = pydotplus.graph_from_dot_data(graphdata)  
Image(graph.create_png())


## 10 Listen

In diesem Kapitel lernen wir einen der nützlichsten eingebauten Datentypen von Python kennen: Listen. Wir lernen auch mehr über Objekte und was passieren kann, wenn es mehr als einen Namen für das gleiche Objekt gibt.

### 10.1 Eine Liste ist eine Folge

Wie eine Zeichenkette, ist eine **Liste** eine Folge (*sequence*) von Werten. In einer Zeichenkette sind die Werte Zeichen; in einer Listen können sie von jedem Typ sein. Die Werte in einer Liste heißen **Elemente**, im Englischen manchmal auch *items*.

Es gibt mehrere Möglichkeiten, eine neue Liste zu erzeugen. Die einfachste ist es, Elemente in eckigen Klammern einzuschließen (`[` und `]`):

In [ ]:
[10, 20, 30, 40]
l = ['crunchy frog', 'ram bladder', 'lark vomit']

Das erste Beispiel ist eine Liste mit vier ganzen Zahlen. Das zweite Beispiel ist eine Liste mit drei Zeichenketten. Die Elemente einer Liste müssen nicht vom gleichen typ sein. Die folgende Liste enthält eine Zeichenkette, eine Gleitkommazhal, eine ganze Zahl und (ja!) eine andere Liste:

In [ ]:
['spam', 2.0, 5, [10, 20]]

Eine Liste innerhalb einer anderen Liste ist **verschachtelt** (*nested*).

Eine Liste, die keine Elemente enthält wird **leere Liste** genannt. Wir können Sie mit Hilfe von leeren Klammern erzeugen:

In [ ]:
[]

Wir Sie vielleicht schon vermutet haben, können wir Listen Variablen zuweisen:

In [ ]:
cheeses = ['Cheddar', 'Edam', 'Gouda']
numbers = [42, 123]
empty = []
print(cheeses, numbers, empty)

### 10.2 Listen sind veränderbar

Die Syntax, um auf Elemente einer Liste zuzugreifen, ist die gleiche wie die zum Zugriff auf die Zeichen einer Zeichenkette: der Klammer-Operator. Der Ausdruck innerhalb der Klammern gibt den Index an. Denken Sie daran, dass die Zählung der Indizes mit 0 beginnt:

In [ ]:
cheeses[0]

Anders als Zeichenketten sind Listen veränderbar. Wenn der Klammer-Operator auf der linken Seite einer Zuweisung auftaucht, identifiziert er das Element der Liste, dessen Wert geändert wird.

In [ ]:
numbers = [42, 123]
numbers[1] = 5
numbers

Das zweite Element von `numbers`, welches 123 war, ist jetzt 5.

Die folgende Abbildung zeigt das Zustandsdiagramm für `cheeses`, `numbers` and `empty`:

![Zustandsdiagramm für drei Listen](zustandsdiagramm_listen.svg)

In diesen Diagrammen sind Listen als Boxen mit dem Wort "Liste" oberhalb und den Elementen der Liste innerhalb repräsentiert. Dabei zeigt `cheeses` auf eine Liste mit drei Elementen, die mit 0, 1 und 2 indiziert sind. `numbers` enthält zwei Elemente; das Diagramm zeigt, dass der Wert des zweiten Elements von 123 zu 5 geändert wurde. `empty` verweist auf eine Liste ohne Elemente.

Listenindizes funktionieren genauso wie Indizes bei Zeichenketten:
- Jeder Ausdruck, der eine ganze Zahl ergibt, kann als Index verwendet werden.
- Wenn wir versuchen, ein Element zu lesen oder zu schreiben, welches nicht existiert, erhalten wir einen `IndexError`.
- Wenn ein Index einen negativen Wert hat, zählt er rückwärts vom Ende der Liste.

Der `in`-Operator funktioniert auch für Listen:

In [ ]:
cheeses = ['Cheddar', 'Edam', 'Gouda']
'Edam' in cheeses

In [ ]:
'Brie' in cheeses

### 10.3 eine Liste durchlaufen

Üblicherweise durchläuft man die Elemente einer Liste mit einer `for`-Schleife. Die Syntax ist die gleiche wie für Zeichenketten:

In [ ]:
for cheese in cheeses:
    print(cheese)

Das funktioniert gut wenn wir die Elemente einer Liste lediglich *lesen* wollen. Wenn wir die Elemente aber schreiben oder verändern wollen, benötigen wir die Indizes. Eine übliche Variante das zu tun ist, die eingebauten Funktionen `range` und `len` zu kombinieren: 

In [ ]:
for i in range(len(numbers)):
    numbers[i] = numbers[i] * 2

Diese Schleife durchläuft die Liste und aktualisiert jedes Element. Dabei gibt `len` die Anzahl der Elemente in der Liste zurück und `range` gibt eine Liste von Indizes zurück, die mit 0 bis $n-1$ numeriert sind - wobei $n$ die Länge der Liste ist. Bei jedem Schleifendurchlauf erhält `i` den Index des nächsten Elements. Die Zuweisung im Rumpf verwendet `i`, um den alten Wert des Elementes zu lesen den neuen Wert zuzuweisen. 

Eine `for`-Schleife über eine leere Liste durchläuft niemals den Schleifenrumpf:

In [ ]:
for x in []:
    print("This never happens.")

Obwohl eine Liste eine andere Liste enthalten kann, zählt die verschachtelte Liste als ein einzelnes Element. Die Länge der folgenden Liste ist vier: 

In [ ]:
allerhand = ['spam', 1, ['Brie', 'Roquefort', 'Pol le Veq'], [1, 2, 3]]
len(allerhand)

### 10.4 Listenoperatoren

Der `+`-Operator verknüpft Listen:

In [ ]:
a = [1,2,3]
b = [4,5,6]
c = a + b
c

Der `*`-Operator wiederholt eine Liste so oft wie angegeben:

In [ ]:
[0] * 4

In [ ]:
[1,2,3] * 3

Das erste Beispiel wiederholt `[0]` viermal. Das zweite Beispiel wiederholt die Liste `[1,2,3]` dreimal.

### 10.5 Listensegmente

Der Segmentoperator (*slice operator*) funktioniert auch auf Listen: 

In [ ]:
t = ['a', 'b', 'c', 'd', 'e', 'f']
t[1:3]

In [ ]:
t[:4]

In [ ]:
t[3:]

Wenn wir den ersten Index weglassen, dann beginnt das Segment mit dem Anfang. Wenn wir den zweiten Index weglassen, dann geht das Segment bis zum Ende. Wenn wir also beide weglassen, dann ist das Segment eine Kopie der gesamten Liste. 

In [ ]:
t[:]

Da Listen veränderbar sind, ist es oft nützlich, eine Kopie der Liste zu erstellen, bevor man Operationen anwendet, die die Liste verändern.

Wenn wir den Segmentoperator auf der linken Seite einer Zuweisung verwenden, können wir mehrere Listenelemente verändern: 

In [ ]:
t = ['a', 'b', 'c', 'd', 'e', 'f']
t[1:3] = ['x', 'y']
t

### 10.6 Listenmethoden

Python stellt Methoden bereit, die auf Listen operieren. Zum Beispiel fügt `append` neue Elemente am Ende einer Liste hinzu:

In [ ]:
t = ['a', 'b', 'c']
t.append('d')
t

`extend` erwartet eine Liste als Argument und fügt alle Elemente der Liste am Ende hinzu:

In [ ]:
t1 = ['a', 'b', 'c']
t2 = ['d', 'e']
t1.extend(t2)
t1

In diesem Beispiel wird `t2` nicht verändert.

Mit `sort` können wir die Elemente einer Liste sortieren - vom kleinsten zum größten:

In [ ]:
t = ['d', 'c', 'e', 'b', 'a']
t.sort()
t

Die meisten Listenmethoden sind leer - sie verändern die Liste und geben `None` zurück. Wenn wir fälschlicherweise `t = t.sort()` schreiben, werden wir vom Ergebnis enttäuscht sein.

### 10.7 Map, filter und reduce

Um die Elemente einer Liste aufzuaddieren, können wir eine Schleife wie die folgende nutzen:

In [ ]:
def add_all(t):
    total = 0
    for x in t:
        total += x
    return total

`total` wird mit 0 initialisiert. Bei jedem Durchlauf der Schleife enthält `x` ein Element der Liste. Der `+=`-Operator ist eine Kurzschreibweise zum Verändern einer Variable. Diese **erweiterte Zuweisung** (*augmented assignment statement*),

```python
total += x
```

ist äquivalent zu 

```python
total = total + x
```

Während die Schleife läuft, akkumuliert `total` die Summe der Elemente. Eine Variable die so verwendet wird, wird manchmal **Akkumulator** genannt.

Die Elemente einer Liste aufzuaddieren ist eine so übliche Operation, dass Python dafür die eingebaute Funktion `sum` bereitstellt:

In [ ]:
t = [1, 2, 3]
sum(t)

Eine Operation wie diese, die eine Folge von Elementen in einen einzelnen Wert kombinbiert, wird manchmal **Reducer** genannt. 

Manchmal wollen wir eine Liste durchlaufen während wir eine andere aufbauen. Beispielsweise erwartet die folgende Funktion eine Liste von Zeichenketten und gibt eine neue Liste zurück, die großgeschriebene Zeichenketten enthält:

In [ ]:
def capitalize_all(t):
    res = []
    for s in t:
        res.append(s.capitalize())
    return res

`res` wird mit der leeren Liste initialisiert. Bei jedem Schleifendurchlauf fügen wir das nächste Element hinzu. Also ist `res` eine andere Art von Akkumulator.

Eine Operation wie `capitalize_all` wird manchmal **Mapper** genannt, da sie eine Funktion auf alle Elemente einer Folge anwendet (*maps*). 

Eine andere übliche Operation ist es, einige Elemente einer Liste auszuwählen und dann eine Teilliste zurückzugeben. Beispielsweise erwartet die folgende Funktion eine Liste von Zeichenketten und gibt eine Liste zurück, die nur die Zeichenketten enthält, die nur aus Großbuchstaben bestehen:

In [ ]:
def only_upper(t):
    res = []
    for s in t:
        if s.isupper():
            res.append(s)
    return res

`isupper` ist eine Zeichenketten-Methode, die `True` zurückgibt, wenn die Zeichenkette nur aus Großbuchstaben besteht.

Eine operation wie `only_upper` wird **Filter** genannt, denn sie wählt einige der Elemente aus und filtert andere heraus.

Die meisten üblichen Listenoperatoren können als eine Kombination aus Mapper, Filter und Reducer ausgedrückt werden.

### 10.8 Elemente löschen

Es gibt mehrere Möglichkeiten, um Elemente aus einer Liste zu entfernen. Wenn wir den Index des Elementes kennen, dann können wir es mittels `pop` entfernen:

In [ ]:
t = ['a', 'b', 'c']
x = t.pop(1)
t

In [ ]:
x

`pop` verändert die Liste und gibt das Element zurück, welches entfernt wurde. Wenn wir keinen Index angeben, dann wird das letzte Element entfernt und zurückgegeben.

Wenn wir den gelöschten Wert nicht benötigen, können wir den `del`-Operator verwenden:

In [ ]:
t = ['a', 'b', 'c']
del t[1]
t

Wenn wir das Element kennen, welches wir entfernen wollen (aber nicht seinen Index), können wir `remove` verwenden:

In [ ]:
t = ['a', 'b', 'c']
t.remove('b')
t

Der Rückgabewert von `remove` ist `None`.

Um mehr als ein Element zu löschen, können wir `del` mit einem einem Segment-Index nutzen:

In [ ]:
t = ['a', 'b', 'c', 'd', 'e', 'f']
del t[1:5]
t

Wie sonst auch, beinhalted das Segment alle Elemente bis zum zweiten Index.

### 10.9 Listen und Zeichenketten

Eine Zeichenkette ist eine Folge von Zeichen und eine Liste ist eine Folge von Werten, aber eine Liste von Zeichen ist nicht das gleiche wie eine Zeichenkette. Um eine Zeichenkette in eine Liste von Zeichen zu konvertieren, können wir die Funktion `list` verwenden:


In [ ]:
s = 'spam'
t = list(s)
t

Da `list` der Name einer eingebauten Funktion ist, sollten wir diesen nicht als Variablennamen verwenden. Da `l` der `1` sehr ähnlich sieht, sollten wir `l` als Name für Listen vielleicht auch verwenden. Daher verwenden wir hier `t`.

Die `list`-Funktion teilt eine Zeichenkette in die individuellen Zeichen auf. Wenn wir eine Zeichenkette in die enthaltenen Wörter aufteilen wollen, können wir die `split`-Methode verwenden:

In [ ]:
s = 'pining for the fjords'
t = s.split()
t

Ein optionales Argument, genannt **Trennzeichen** (*delimiter*) gibt an, welche Zeichen als Wortgrenzen verwendet werden sollen. Im folgenden Beispiel wird ein Bindestrich als Trennzeichen verwenden:

In [ ]:
s = 'spam-spam-spam'
delimiter = '-'
t = s.split(delimiter)
t

Das Gegenstück zu `split` ist `join`. Die Methode erwartet eine Liste von Zeichenketten und verkettet die einzelnen Elemente. `join` ist eine Zeichenketten-Methode, daher müssen wir sie auf ein Trennzeichen anwenden und die Liste als Parameter übergeben:

In [ ]:
t = ['pining', 'for', 'the', 'fjords']
delimiter = ' '
s = delimiter.join(t)
s

In diesem Fall ist das Trennzeichen das Leerzeichen, so dass `join` ein Leerzeichen zwischen die Wörter setzt. Um die Zeichenketten ohne Trennzeichen miteinander zu verketten, können wir die leere Zeichenkette  `''` als Trennzeichen verwenden.

### 10.10. Objekte und Werte

Wenn wir diese beiden Zuweisungen ausführen:

In [ ]:
a = 'banana'
b = 'banana'

wissen wir, dass sowohl `a` als auch `b` auf eine Zeichenkette verweisen, aber wir wissen nicht, ob sie auf *die selbe* Zeichenkette verweisen. Es gibt zwei mögliche Zustände:

![Zustandsdiagramm für zwei Zeichenketten](https://amor.cms.hu-berlin.de/~jaeschkr/teaching/spp/zustandsdiagramm_zeichenketten.svg)

Im ersten Fall verweisen `a` und `b` auf zwei unterschiedliche Objekte, die den gleichen Wert haben. Im zweiten Fall verweisen sie auf das selbe Objekt.

Um zu prüfen, ob zwei Variablen auf das selbe Objekt verweisen, können wir den `is`-Operator verwenden:

In [ ]:
a = 'banana'
b = 'banana'
a is b

In diesem Beispiel erzeugt Python nur ein Zeichenketten-Objekt und sowohl `a` als auch `b` verwiesen darauf. Wenn wir jedoch zwei Listen erzeugen, erhalten wir zwei Objekte:

In [ ]:
a = [1, 2, 3]
b = [1, 2, 3]
a is b

Das Zustandsdiagramm sieht in diesem Fall so aus:

![Zustandsdiagramm für zwei Listen](https://amor.cms.hu-berlin.de/~jaeschkr/teaching/spp/zustandsdiagramm_listen_ab.svg)

In diesem Fall würden wir sagen, dass die beiden Listen **äquivalent** sind, denn sie enthalten die gleichen Elemente, aber sie sind nicht **identisch**, denn sie sind nicht das selbe Objekt. Wenn zwei Objekte identisch sind, sind sie auch äquivalent; aber wenn sie äquivalent sind, sind sie nicht notwendig auch identisch.

Bis jetzt haben wir die Begriffe "Objekt" und "Wert" synonym verwendet, aber es ist eigentlich präziser, zu sagen, dass ein Objekt einen Wert hat. Wenn wir `[1,2,3]` evaluieren, dann erhalten wir ein Listenobjekt, dessen Werte eine Folge von ganzen Zahlen darstellen. Wenn ein anderes Listenobjekt die gleichen Elemente enthält sagen wir, dass es den gleichen Wert hat, aber es ist nicht das selbe Objekt.

### 10.11 Aliasing

Wenn `a` auf ein Objekt verweist und wir die Zuweisung `b = a` ausführen, dann verweisen beide Variablen auf das selbe Objekt:

In [ ]:
a = [1, 2, 3]
b = a
b is a

Das Zustandsdiagramm schaut dann folgendermaßen aus:

![Zustandsdiagramm für zwei Listen](https://amor.cms.hu-berlin.de/~jaeschkr/teaching/spp/zustandsdiagramm_listen_ab2.svg)

Die Verbindung (*association*) einer Variable mit einem Objekt wird **Referenz** (*reference*) genannt. In diesem Beispiel gibt es zwei Referenzen auf das selbe Objekt.

Ein Objekt mit mehr als einer Referenz hat mehr als einen Namen, daher sagen wir, dass dieses Objekt einen **Alias** besitzt. 

Falls das Objekt mit Alias veränderbar ist, dann betreffen Veränderungen, die an einem Alias vorgenommen werden auch den anderen:


In [ ]:
b[0] = 42
a

Obwohl dieses Verhalten nützlich sein kann, ist es auch fehleranfällig. Im allgemeinen ist es sicherer, Aliasing zu vermeiden wenn wir mit veränderbaren Objekten arbeiten.

Bei unveränderbaren Objekte wie z.B. Zeichenketten ist Aliasing kein großes Problem. Im Beispiel
```python
a = 'banana'
b = 'banana'
```
macht es so gut wie nie einen Unterschied, ob `a` und `b` auf die gleiche Zeichenkette verweisen oder nicht.

### 10.12 Listen als Argumente

Wenn wir eine Liste an eine Funktion als Argument übergeben, erhält die Funktion eine Referenz auf die Liste. Wenn die Funktion die Liste verändert, verändert sich auch die Liste an der aufrufenden Stelle (denn es ist die selbe Liste). Beispielsweise entfernt die Funktion `delete_head` das erste Element einer Liste:

In [ ]:
def delete_head(t):
    del t[0]

Hier sehen wir, wie die Funktion verwendet werden kann und wie sie wirkt:

In [ ]:
letters = ['a', 'b', 'c']
delete_head(letters)
letters

Der Parameter `t` und die Variable `letters` sind Aliase für das selbe Objekt. Das Stapeldiagramm beim Aufruf von `delete_head` sieht folgendermaßen aus:

![Stapeldiagramm delete_head](https://amor.cms.hu-berlin.de/~jaeschkr/teaching/spp/stapeldiagramm_delete_head.svg)

Die zwei Blöcke `__main__` und `delete_head` teilen sich die Liste, daher zeigen zwei Pfeile auf sie.

Es ist wichtig, dass wir zwischen Operationen unterscheiden, die Listen *verändern* und jenen, die neue Listen *erzeugen*. Beispielsweise verändert die Methode `append` eine Liste, aber der Operator `+` erzeugt eine neue Liste.

Nachfolgend ein Beispiel zu `append`:

In [ ]:
t1 = [1, 2]
t2 = t1.append(3)
print(t1)
print(t2)

Der Rückgabewert von `append` ist `None`.

Nachfolgend ein Beispiel für den Operator `+`:

In [ ]:
t3 = t1 + [4]
print(t1)
print(t3)

Das Ergebnis des Operators ist eine neue Liste; die Ursprungsliste ist unverändert.

Dieser Unterschied ist wichtig, wenn wir Funktionen schreiben die Listen verändern. Beispielsweise entfernt die folgende Funktion *nicht* das erste Element einer Liste: 

In [ ]:
def bad_delete_head(t):
    t = t[1:]              # FALSCH!

Der Segmentoperator erzeugt eine neue Liste und die Zuweisung sorgt dafür, dass `t` auf die neue Liste verweist, aber das verändert nicht die Ursprungsliste:

In [ ]:
t4 = [1, 2, 3]
bad_delete_head(t4)
t4

Am Anfang von `bad_delete_head` verweisen `t` und `t4` auf die gleiche Liste. Am Ende verweist `t` auf eine neue Liste, aber `t4` verweist immer noch auf die ursprüngliche, unveränderte Liste.

Eine Alternative ist, eine Funktion zu schreiben, die eine neue Liste erzeugt und zurückgibt. Beispielsweise gibt `tail` alle bis auf das erste Element einer Liste zurück:

In [ ]:
def tail(t):
    return t[1:]

Diese Funktion verändert die Ursprungsliste nicht! Folgendermaßen kann die Funktion verwendet werden:

In [ ]:
letters = ['a', 'b', 'c']
rest = tail(letters)
rest

### 10.13 Debugging

Unvorsichtige Verwendung von Listen (und anderen veränderbaren Objekten) kann langwieriges Debuggen verursachen. Einige übliche Fehler und Wege, sie zu vermeiden:

#### 1. Die meisten Listenmethoden verändern das Argument und geben `None` zurück.

Das ist das Gegenteil zum Verhalten der Methoden für Zeichenketten, die eine neue Zeichenkette zurückgeben und die ursprüngliche Zeichenkette unverändert lassen.

Wenn Sie gewohnt sind, Code für Zeichenketten so zu schreiben:
   
```python
word = word.strip()
```
   
Dann ist es verlpckend, folgenden Code für Listen zu schreiben:
   
```python
t = t.sort()      # FALSCH!
```
   
Weil `sort` keinen Wert (also `None`) zurückliefert, wird die nächste Operation, die wir mit `t` durchführen würden wahrscheinlich fehlschlagen. 
   
Bevor wir Methoden und Operatoren für Listen verwenden, sollten wir aufmerksam die Dokumentation lesen und mit etwas Beispielcode testen.
   
#### 2. Sich für ein Idiom entscheiden und dann dabei bleiben.

Ein Teil des Problems mit Listen ist, dass es zu viele Möglichkeiten gibt, mit Ihnen umzugehen. Beispielsweise können wir zum Entfernen eines Elements `pop`, `remove`, `del` oder sogar den Segmentoperator verwenden. 
   
Um ein Element hinzuzufügen, können wir die Methode `append` oder den Operator `+` verwenden. Angenommen, `t` ist eine Liste und `x` ist ein Listenelement, dann sind die folgenden Varianten korrekt:

In [ ]:
t = ['a', 'b', 'c']
x = 'n'

t.append(x)
print(t)

t = t + [x]
print(t)

t += [x]
print(t)

und die folgenden sind falsch:

In [ ]:
t.append([x])          # FALSCH!
print(t)

t = t.append(x)        # FALSCH!
print(t)

t + [x]                # FALSHC!
print(t)

t = t + x              # FLASCH!
print(t)

Probieren Sie diese Beispiele (einzeln!) aus und stellen Sie sicher, dass Sie wirklich verstanden haben, was sie tun. Beachten Sie, dass nur das letzte Beispiel einen Laufzeitfehler (*runtime error*) verursacht. Die anderen drei Varianten sind erlaubt, aber sie tun das Falsche.
   
#### 3. Kopien erzeugen, um Aliasing zu vermeiden.

Wenn Sie eine Methode wie z.B. `sort` verwenden wollen, die das Argument verändert, aber Sie benötigen auch die Ursprungsliste, dann können Sie eine Kopie erzeugen:

In [ ]:
t = [3, 1, 2]
t2 = t[:]
t2.sort()
print(t)
print(t2)

In diesem Beispiel könnten Sie auch die eingebaute Funktion `sorted` verwenden, die eine neue, sortierte Liste zurückgibt, ohne die Ursprungsliste zu verändern: 

In [ ]:
t2 = sorted(t)
print(t)
print(t2)

### 10.14 Glossar

Legen wir uns eine Liste mit den wichtigsten Begriffen an, die wir im Kapitel 10 gelernt haben:

- Liste: eine Folge von Werten
- Element:
- verschachtelte Liste: 
- Akkumulator:
- erweiterte Zuweisung
- Reducer:
- Mapper:
- Filter:
- Objekt:
- äquivalent:
- identisch:
- Referenz:
- Aliasing:
- Trennzeichen:

Ergänzen Sie die Liste in eigenen Worten. Das ist eine gute Erinnerungs- und Übungsmöglichkeit.

### 10.15 Übung

Sie finden die Lösungen für die Aufgaben hier: http://thinkpython2.com/code/list_exercises.py

#### Aufgabe 1
Schreiben Sie eine Funktion `nested_sum`, die eine Liste von Listen von ganzen Zahlen erwartet und die Werte der einzelnen Elemente aufaddiert und das Ergebnis zurückgibt. Beispielsweise sollte die Funktion für die Liste `t = [[1, 2], [3], [4, 5, 6]]` den Wert `21` zurückgeben.

In [ ]:

def nested_sum(t):
    # Implementieren Sie hier die Funktion
    

#### Aufgabe 2
Schreiben Sie eine Funktion `cumsum`, die eine Liste von Zahlen erwartet und die kumulative Summe zurückgibt, d.h. eine neue Liste, in der das *i*te Element die Summe der ersten *i + 1* Elemente der Original-Liste enthält. Beispielsweise sollte die Funktion für die Liste `t = [1, 2, 3]` die Liste `[1, 3, 6]` zurückgeben.

In [ ]:
def cumsum(t):
    # Implementieren Sie hier die Funktion

Testen Sie die Funktion mit verschiedenen Listen als Eingabe.

Welche Liste müssten Sie der Funktion `cumsum` übergeben, um als Ergebnis die Liste `[1, 1, 2, 3, 5, 8, 13, 21, 34, 55]` der ersten zehn Fibonacci-Zahlen zu erhalten?

#### Aufgabe 3
Schreiben Sie eine Funktion `middle`, die eine Liste als Argument erwartet und eine neue Liste zurückgibt, die alle Elemente bis auf das erste und letzte der Ausgangsliste enthält. Beispielsweise sollte die Funktion für die Liste `t = [1,2,3,4]` die Liste `[2,3]` zurückgeben:

```python
t = [1,2,3,4]
middle(t)
```
sollte `[2,3]` ergeben.

In [ ]:
def middle(t):
    # Implementieren Sie hier die Funktion

#### Aufgabe 4
Schreiben Sie eine Funktion `chop`, die eine Liste als Argument erwartet, das erste und letzte Element entfernt und `None` zurückgibt. Beispielsweise sollte

```python
t = [1,2,3,4]
chop(t)
t
```
`[2,3]` ergeben.

In [ ]:
def chop(t):
    # Implementieren Sie hier die Funktion

#### Aufgabe 5
Schreiben Sie eine Funktion `is_sorted`, die eine Liste als Argument erwartet und `True` zurückgibt, falls die Liste in aufsteigender Reihenfolge sortiert ist und ansonsten `False`. Also zum Beispiel:

```python
>>> is_sorted([1, 2, 2])
True
>>> is_sorted(['b', 'a'])
False
```

In [ ]:
def is_sorted(t):
    # Implementieren Sie hier die Funktion

#### Aufgabe 6
Zwei Wörter bilden ein *Anagramm*, wenn wir die Buchstaben des einen Wortes so umordnen können, dass sich das andere Wort ergibt. (Beispielsweise bilden *LAGER* und *REGAL* ein Anagramm.) Schreiben Sie eine Funktion `is_anagram`, die zwei Zeichenketten erwartet und `True` zurückgibt, falls sie ein Anagramm bilden (sonst `False`). 

In [ ]:
def is_anagram(v, w):
    # Implementieren Sie hier die Funktion

Zusatzaufgabe: Suchen Sie in der Wortliste aus dem [8. Kapitel](seminar08.ipynb) nach Anagrammen.

#### Aufgabe 7
Schreiben Sie eine Funktion `has_duplicates`, die eine Liste als Argument erwartet und `True` zurückgibt, falls ein Element der Liste mehr als einmal in der Liste enthalten ist. Die Funktion soll die Ursprungsliste nicht verändern.

In [ ]:
def has_duplicates(t):
    # Implementieren Sie hier die Funktion

#### Aufgabe 8
In dieser Aufgabe geht es um das sogenannte "Geburtstags-Paradoxon" über das Sie mehr in [Wikipedia](http://en.wikipedia.org/wiki/Birthday_paradox) lesen können.

Wenn 23 Studierende in Ihrem Kurs sind, wie hoch ist dann die Wahrscheinlichkeit, dass zwei davon am gleichen Tag Geburtstag haben? Sie können diese Wahrscheinlichkeit schätzen, indem Sie zufällig 23 Geburtstage auswürfeln und prüfen, ob mindestens zwei davon identisch sind. (*Hinweis: Sie können zufällige Geburtstage mit Hilfe der Funktion `randint` aus dem [Modul `random`](https://docs.python.org/3.5/library/random) erzeugen.)

Eine Lösung für diese Aufgabe finden Sie hier: http://thinkpython2.com/code/birthday.py

In [ ]:
from random import randint

# Implementieren Sie hier Ihr Programm

#### Aufgabe 9
Schreiben Sie eine Funktion, die die Datei "top10000de.txt" einliest (siehe [Abschnitt 9.1](seminar09.ipynb#9.1-Wortlisten-einlesen)) und daraus eine Liste erzeugt mit den Wörtern als Elementen erzeugt. Implementieren Sie zwei Versionen dieser Funktion: eine, die die Methode `append` verwendet und eine, die den Operator `+` mittels `t = t + [t]` verwendet. Welche der beiden Versionen hat eine größere Laufzeit? Warum?

Eine Lösung für diese Aufgabe finden Sie hier: http://thinkpython2.com/code/wordlist.py

In [ ]:
# Implementieren Sie hier die beiden Varianten Ihrer Funktion

#### Aufgabe 10

Um zu überprüfen, ob ein Wort in einer Wortliste ist, können wir den Operator `in` verwenden, aber das wäre recht langsam, denn der Operator muss dazu die Liste linear durchlaufen.

Wenn wir mit einer sortierten Liste arbeiten, können wir den Vorgang beschleunigen, indem wir *binäre Suche* (auch bekannt als *bisection search*) verwenden. Das entspricht dem Verfahren, welches wir verwenden, wenn wir ein Wort in einem Wörterbuch nachschlagen: wir beginnen in der Mitte und schauen, ob das gesuchte Wort vor dem Wort in der Mitte der Liste stehen müsste. Falls dem so ist, durchsuchen wir die erste Hälfte der Liste auf die gleiche Art, ansonsten durchsuchen wir die zweite Hälfte.

In jedem Fall halbieren wir damit den Suchraum. Im Fall unserer Wortliste mit 10000 Wörtern benötigen wir höchstens 13 Schritte, um das gesuchte Wort zu finden oder festzustellen, dass die Liste das Wort nicht enthält. 

Schreiben Sie eine Funktion `binary_search` die eine sortierte Liste sowie ein Wort als Argumente erwartet und `True` zurückgibt, falls das Wort in der Liste enthalten ist, ansonsten `False`.

Alternativ können Sie auch die [Dokumentation für das Modul `bisect`](https://docs.python.org/3.5/library/bisect) lesen und dieses verwenden. Eine Lösung finden Sie hier: http://thinkpython2.com/code/inlist.py

In [ ]:
def binary_search(t, w):
    # Implementieren Sie hier die Funktion

# Hinweis: Sie müssen die Liste sortieren, damit 
# binary_search funktioniert. Dies geht mittels
# der Funktion sort - siehe help(list.sort)

#### Aufgabe 11
Zwei Wörter sind ein "umgekehrtes Paar" (*reverse pair*), wenn jedes Wort rückwärts gelesen das jeweils andere ergibt (wie bei "LAGER" und "REGAL"). Schreiben Sie ein Programm, welches alle umgekehrten Paare in unserer Wortliste findet. (Ignorieren Sie dabei wieder Groß- und Kleinschreibung.) Eine Lösung finden Sie hier: http://thinkpython2.com/code/reverse_pair.py

(*Hinweis: Sie werden einige doppelte Paare finden, was daran liegt, dass in top10000.txt Groß- und Kleinschreibung unterschieden wird.*)

In [ ]:
# Implementieren Sie hier Ihr Programm


#### Aufgabe 12
Zwei Wörter "greifen ineinander" (*interlock*), wenn sich durch abwechselndes Hinzufügen eines Buchstabens aus beiden Wörtern ein neues Wort ergibt. Beispielsweise greifen "Mai" und "im" ineinander und bilden das Wort "Miami". 

![Mai + im = Miami](https://amor.cms.hu-berlin.de/~jaeschkr/teaching/spp/miami.svg)

1. Schreiben Sie ein Program, welches alle Wortpaare findet, die ineinandergreifen. Hinweis: durchlaufen Sie nicht alle möglichen Wortpaare!
2. Gibt es Wörter, die dreifach ineinandergreifen; das heißt, jeder dritte Buchstabe ergibt ein Wort, beginnend mit dem ersten, zweiten oder dritten Buchstaben? (*Leider ist unsere Wortliste mit 10000 Wörtern recht kurz ... als einziges einigermaßen sinnvolles Beispiel ergibt sich "bekommt", welches die "Wörter" "Bot", "EM", und "km" enthält.*)

(Diese Aufgabe wurde durch ein Beispiel auf http://puzzlers.org/ inspiriert, eine Lösung finden Sie hier: http://thinkpython2.com/code/interlock.py)


In [ ]:
# Implementieren Sie hier das Programm

![Speichern](https://amor.cms.hu-berlin.de/~jaeschkr/teaching/spp/floppy.png) Speichern Sie dieses Notebook, so dass Ihre Änderungen nicht verlorengehen (nicht auf einem Pool-Rechner). 
Klicken Sie dazu oben links auf das Disketten-Icon und nutzen Sie beispielsweise einen USB-Stick, E-Mail, Google Drive, Dropbox oder Ihre [HU-Box](https://box.hu-berlin.de/).  

![Smiley](https://upload.wikimedia.org/wikipedia/commons/thumb/7/79/Face-smile.svg/48px-Face-smile.svg.png)

Herzlichen Glückwunsch! Sie haben das 10. Kapitel geschafft. Weiter geht es in [11: assoziative Felder](seminar11.ipynb).